In [1]:
# Stop warnings
# -------------
import warnings
warnings.filterwarnings("ignore")

# General imports
# ---------------
import os
import sys
import json
import glob
import numpy as np
import matplotlib.pyplot as pl
import ipdb
import platform
import h5py
import scipy.io
opj = os.path.join
deb = ipdb.set_trace

# Bokeh imports
# ---------------
from bokeh.io import output_notebook, show, save, output_file, export_png, export_svgs
from bokeh.layouts import row, column, gridplot
output_notebook()

# Functions import
# ----------------
from plot_class import PlotOperator
from utils import set_pycortex_config_file

# Bokeh imports
# ---------------
from bokeh.io import output_notebook, show, save, output_file, export_png, export_svgs
from bokeh.layouts import row, column, gridplot

# Popeye imports
import popeye.utilities as utils
from popeye.visual_stimulus import VisualStimulus
import popeye.css as css
import popeye.og as og

# Check system
# ------------
sys.exit('Drawing Flatmaps only works with Python 3. Aborting.') if sys.version_info[0] > 3 else None

# Get inputs
# ----------
subject = 'sub-01'
acq = 'acq-2p5mm'
fit_model = 'gauss'
save_svg = 0

# Define analysis parameters
# --------------------------
with open('../settings.json') as f:
    json_s = f.read()
    analysis_info = json.loads(json_s)

# Define folders and settings
# ---------------------------
base_dir = analysis_info['base_dir_local']
prf_signs = analysis_info['prf_signs']
rois = analysis_info['rois']
deriv_dir = "{base_dir}/pp_data/{subject}/{fit_model}/deriv".format(base_dir = base_dir, subject = subject, fit_model = fit_model)
h5_dir = "{base_dir}/pp_data/{subject}/{fit_model}/h5".format(base_dir = base_dir, subject = subject, fit_model = fit_model)
bokeh_dir = "{base_dir}/pp_data/{subject}/{fit_model}/bokeh_outputs".format(base_dir = base_dir, subject = subject, fit_model = fit_model)
try: os.makedirs(bokeh_dir)
except: pass

# Create stimulus design
# ----------------------
visual_dm_file = scipy.io.loadmat("{base_dir}/pp_data/visual_dm/vis_design.mat".format(base_dir = base_dir))
visual_dm = visual_dm_file['stim']
stimulus = VisualStimulus(  stim_arr = visual_dm,
                            viewing_distance = analysis_info["screen_distance"],
                            screen_width = analysis_info["screen_width"],
                            scale_factor = 1/10.0,
                            tr_length = analysis_info["TR"],
                            dtype = np.short)

if fit_model == 'gauss':
    fit_func = og.GaussianFit
    model_func = og.GaussianModel(  stimulus = stimulus,
                                    hrf_model = utils.spm_hrf)
    step_r2 = [0,100/3.0,250/3.0,100]
    list_r2_level = ['High','Low']
    step_params = [0,100/3.0,200/3.0,100]
    list_params_level = ['High','Low']
    list_params = ['ecc','amp','size','cov']
    num_plots = len(list_params)*len(step_params)*(len(step_r2)-1)
    
elif fit_model == 'css':
    fit_func = css.CompressiveSpatialSummationFit
    model_func = css.CompressiveSpatialSummationModel(  stimulus = stimulus,
                                                        hrf_model = utils.spm_hrf)
    step_r2 = [0,100/3.0,200/3.0,100]
    list_r2_level = ['Low','High']
    step_params = [0,100/3.0,200/3.0,100]
    list_params_level = ['Low','High']
    list_params = ['ecc','amp','size','cov','non_lin']

    num_plots = len(list_params)*len(step_params)*(len(step_r2)-1)
    
model_func.hrf_delay = 0

Loading BokehJS ...

In [2]:
# Draw main analysis figure
# -------------------------
print('creating bokeh plots')
sign_idx, rsq_idx, ecc_idx, polar_real_idx, polar_imag_idx , size_idx, \
            non_lin_idx, amp_idx, baseline_idx, cov_idx, x_idx, y_idx = 0,1,2,3,4,5,6,7,8,9,10,11


# Initialize data
# ---------------
for roi_num, roi in enumerate(rois):
    for prf_sign in prf_signs:
        
        tc_mat = []

        # create html folder
        exec("html_dir_{prf_sign} = '{bokeh_dir}/html/{prf_sign}'".format(bokeh_dir = bokeh_dir, prf_sign = prf_sign))
        try: exec('os.makedirs(html_dir_{prf_sign})'.format(prf_sign = prf_sign))
        except: pass

        # create svg folder
        if save_svg == 1:
            exec("svg_dir_{prf_sign} = '{bokeh_dir}/svg/{prf_sign}'".format(bokeh_dir = bokeh_dir, prf_sign = prf_sign))
            try: os.makedirs('os.makedirs(svg_dir_{prf_sign})'.format(prf_sign = prf_sign))
            except: pass
            exec('svg_folder = svg_dir_{prf_sign}'.format(prf_sign = prf_sign))

        # load h5 file
        h5_file = h5py.File("{h5_dir}/{roi}_{acq}.h5".format(h5_dir = h5_dir, roi = roi, acq = acq))

        # load deriv data
        deriv_data_name = "prf_deriv_{acq}_{prf_sign}".format(acq = acq, prf_sign = prf_sign)
        deriv_data = h5_file['{folder_alias}/{data_name}'.format(folder_alias = prf_sign, data_name = deriv_data_name)]
        
        # load time course data
        tc_data_name = "{subject}_task-AttendStim_{acq}_fmriprep_sg_psc_avg".format(subject = subject, acq = acq)
        tc_data = h5_file['{folder_alias}/{data_name}'.format(folder_alias = prf_sign, data_name = tc_data_name)]

        # load coordinates data
        coord_data_name = "coord"
        coord_data = h5_file['{folder_alias}/{data_name}'.format(folder_alias = prf_sign, data_name = coord_data_name)]
        
        # threshold data

        voxel_num_ini = deriv_data.shape[0]
        voxel_num = 0
        if voxel_num_ini > 0:
            # take out nan
            deriv_data = deriv_data[~np.isnan(deriv_data[:,rsq_idx]),:]
            tc_data = tc_data[~np.isnan(deriv_data[:,rsq_idx]),:]
            coord_data = coord_data[~np.isnan(deriv_data[:,rsq_idx]),:]
            
            # threshold on eccentricity and size
            deriv_data_th = deriv_data
            size_th_down = deriv_data_th[:,size_idx] >= analysis_info['size_th'][0]
            size_th_up = deriv_data_th[:,size_idx] <= analysis_info['size_th'][1]
            ecc_th_down = deriv_data_th[:,ecc_idx] >= analysis_info['ecc_th'][0]
            ecc_th_up = deriv_data_th[:,ecc_idx] <= analysis_info['ecc_th'][1]
            all_th = np.array((size_th_down,size_th_up,ecc_th_down,ecc_th_up)) 

            deriv_data = deriv_data[np.logical_and.reduce(all_th),:]
            tc_data = tc_data[np.logical_and.reduce(all_th),:]
            coord_data = coord_data[np.logical_and.reduce(all_th),:]
            voxel_num = deriv_data.shape[0]
        
        # Draw and save figures
        # ---------------------
        if voxel_num > 0:
            # randomize order and take 10 %
            new_order = np.random.permutation(voxel_num)
            deriv_data = deriv_data[new_order,:]
            tc_data = tc_data[new_order,:]
            coord_data = coord_data[new_order,:]
            
            print("drawing {roi}_{prf_sign} figures, n = {voxel_num}".format(roi = roi, voxel_num = voxel_num, prf_sign = prf_sign)) 

            data_source = { 'sign': deriv_data[:,sign_idx],
                            'rsq': deriv_data[:,rsq_idx],
                            'ecc': deriv_data[:,ecc_idx],
                            'sigma': deriv_data[:,size_idx],
                            'non_lin': deriv_data[:,non_lin_idx],
                            'beta': deriv_data[:,amp_idx],
                            'baseline': deriv_data[:,baseline_idx],
                            'cov': deriv_data[:,cov_idx],
                            'x': deriv_data[:,x_idx],
                            'y': deriv_data[:,y_idx],
                            'colors_ref': deriv_data[:,ecc_idx]}

            param_all = {   'roi_t': roi, 
                            'p_width': 400, 
                            'p_height': 400, 
                            'min_border_large': 10, 
                            'min_border_small': 5,
                            'bg_color': tuple([229,229,229]), 
                            'stim_color': tuple([250,250,250]), 
                            'hist_fill_color': tuple([255,255,255]),
                            'hist_line_color': tuple([0,0,0]), 
                            'stim_radius': analysis_info['stim_width']/2,
                            'cmap': 'Spectral',
                            'cmap_steps': 8,
                            'col_offset': 0,
                            'vmin': 0,
                            'vmax': 8,
                            'leg_xy_max_ratio': 1.8,
                            'dataMat': deriv_data,
                            'data_source': data_source,
                            'hist_range': (0,0.5),
                            'hist_steps': 0.5,
                            'h_hist_bins': 16,
                            'link_x': False,
                            'link_y': False,
                            'save_svg': save_svg
                            }

            if save_svg == 1:
                param_all.update({'svg_folder': svg_folder})

            plotter = PlotOperator(**param_all)
            
            # pRFmap
            title = '{roi} {prf_sign}: pRF map (n = {voxel_num})'.format(roi = roi, voxel_num = voxel_num, prf_sign = prf_sign)
            params_pRFmap = param_all

            params_pRFmap.update({   
                            'x_range': (-15, 15),
                            'y_range': (-15, 15),
                            'x_label': 'Horizontal coordinate (dva)',
                            'y_label': 'Vertical coordinate (dva)',
                            'x_source_label': 'x',
                            'y_source_label': 'y',
                            'x_tick_steps': 5,
                            'y_tick_steps': 5,
                            'v_hist_bins': 12,
                            'h_hist_bins': 12,
                            'main_fig_title': title})
            if save_svg == 1:
                params_pRFmap.update({'svg_filename': '{roi}_{prf_sign}_pRFmap'.format(prf_sign = prf_sign, roi= roi)})

            f_pRFmap, old_main_fig1 = plotter.draw_figure(  parameters = params_pRFmap, 
                                                            plot = 'map')

            
            # pRF cov
            title = '{roi} {prf_sign}: pRF density map'.format(roi = roi, prf_sign = prf_sign)
            params_pRFcov = param_all
            params_pRFcov.update({   
                            'x_range': (-15, 15), 
                            'y_range': (-15, 15),
                            'x_label': 'Horizontal coordinate (dva)',
                            'y_label': 'Vertical coordinate (dva)',
                            'x_tick_steps': 5,
                            'y_tick_steps': 5,
                            'smooth_factor': 15,
                            'cmap': 'viridis',
                            'cmap_steps': 10,
                            'col_offset': 0,
                            'vmin': 0,
                            'vmax': 1,
                            'cb_tick_steps': 0.2,
                            'condition': 'cov',
                            'cb_label': 'pRF coverage (norm.)',
                            'link_x': True,
                            'link_y': True})
            if save_svg == 1:
                params_pRFcov.update({'svg_filename': '{roi}_{prf_sign}_pRFcov'.format(prf_sign = prf_sign, roi= roi)})
                        
            params_pRFcov.update({'main_fig_title':   title})

            f_pRFcov, old_main_fig1 = plotter.draw_figure(parameters = params_pRFcov, 
                                           plot = 'cov',
                                           old_main_fig = old_main_fig1)

            all_fig1 = gridplot([ [f_pRFmap,f_pRFcov]], toolbar_location = 'right')
            dddd

creating bokeh plots
drawing V1_pos figures, n = 319


TypeError: 'Column' object does not support indexing

In [ ]:
f_pRFcov

In [7]:
show(all_fig1)